<a href="https://colab.research.google.com/github/HimanshiBaliyan/SER/blob/main/KDE.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install cartopy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 13.4 MB/s eta 0:00:00


In [ ]:
!pip install folium


In [ ]:
import pandas as pd
import numpy as np
import re
from scipy.stats import gaussian_kde
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
from cartopy.feature import STATES, BORDERS

In [ ]:
import pandas as pd
import geopandas as gpd
import folium
from shapely.geometry import Point

In [ ]:
from builtins import map

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df = pd.read_csv(r"/content/drive/MyDrive/SerDataset/csvData/fear_loc.csv")
df.head()

Emotion                                               Path       Latitude  \
0    fear  /content/drive/MyDrive/SerDataset/Tess/YAF_fea...  N 8° 52′ 52''   
1    fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...  N 8° 57′ 24''   
2    fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...  N 8° 47′ 40''   
3    fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...  N 28° 33′ 7''   
4    fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...  N 28° 51′ 9''   

       Longitude  
0  E 76° 35′ 4''  
1  E 76° 51′ 9''  
2  E 76° 40′ 4''  
3  E 77° 5′ 54''  
4  E 77° 4′ 43''

In [ ]:
df.tail()

Emotion                                               Path  \
1923    fear  /content/drive/MyDrive/SerDataset/Crema/1051_T...   
1924    fear  /content/drive/MyDrive/SerDataset/Crema/1044_M...   
1925    fear  /content/drive/MyDrive/SerDataset/Savee/DC_f06...   
1926    fear  /content/drive/MyDrive/SerDataset/Crema/1056_W...   
1927    fear  /content/drive/MyDrive/SerDataset/Crema/1056_T...   

            Latitude       Longitude  
1923    N 34° 9′ 0''   E 74° 52′ 0''  
1924    N 34° 5′ 0''   E 74° 50′ 0''  
1925  N 30° 13′ 20''   E 78° 47′ 0''  
1926  N 33° 59′ 13''  E 74° 46′ 27''  
1927    N 34° 5′ 8''  E 74° 48′ 20''

In [ ]:
def dms_to_dd(coordinate):
    parts = re.split(r'\s+', coordinate)
    direction = parts[0]
    deg, minutes, seconds = map(float, re.findall(r'\d+', coordinate))
    return (deg + minutes / 60 + seconds / 3600) * (1 if direction in ['N', 'E'] else -1)

In [ ]:
print(dms_to_dd("N 28° 48′ 1''"))

28.80027777777778


In [ ]:
df.isnull().sum()

Emotion      0
Path         0
Latitude     0
Longitude    0
dtype: int64

In [ ]:
df.dropna(subset=['Latitude', 'Longitude'], inplace=True)

In [ ]:
df.isnull().sum()

Emotion      0
Path         0
Latitude     0
Longitude    0
dtype: int64

In [ ]:
df['Latitude_DD'] = df['Latitude'].apply(dms_to_dd)
df['Longitude_DD'] = df['Longitude'].apply(dms_to_dd)
print(df)

     Emotion                                               Path  \
0       fear  /content/drive/MyDrive/SerDataset/Tess/YAF_fea...   
1       fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...   
2       fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...   
3       fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...   
4       fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...   
...      ...                                                ...   
1923    fear  /content/drive/MyDrive/SerDataset/Crema/1051_T...   
1924    fear  /content/drive/MyDrive/SerDataset/Crema/1044_M...   
1925    fear  /content/drive/MyDrive/SerDataset/Savee/DC_f06...   
1926    fear  /content/drive/MyDrive/SerDataset/Crema/1056_W...   
1927    fear  /content/drive/MyDrive/SerDataset/Crema/1056_T...   

            Latitude       Longitude  Latitude_DD  Longitude_DD  
0      N 8° 52′ 52''   E 76° 35′ 4''     8.881111     76.584444  
1      N 8° 57′ 24''   E 76° 51′ 9''     8.956667     76.852500

In [ ]:
valid_latitude_range = (-90, 90)
valid_longitude_range = (-180, 180)
invalid_latitude = df[(df['Latitude_DD'] < valid_latitude_range[0]) | (df['Latitude_DD'] > valid_latitude_range[1])]
invalid_longitude = df[(df['Longitude_DD'] < valid_longitude_range[0]) | (df['Longitude_DD'] > valid_longitude_range[1])]
print("Invalid latitude values:\n", invalid_latitude)
print("Invalid longitude values:\n", invalid_longitude)

Invalid latitude values:
 Empty DataFrame
Columns: [Emotion, Path, Latitude, Longitude, Latitude_DD, Longitude_DD]
Index: []
Invalid longitude values:
 Empty DataFrame
Columns: [Emotion, Path, Latitude, Longitude, Latitude_DD, Longitude_DD]
Index: []


In [ ]:
if not invalid_latitude.empty:
    df = df[~invalid_latitude.index]
if not invalid_longitude.empty:
    df = df[~invalid_longitude.index]

In [ ]:
print(df)

     Emotion                                               Path  \
0       fear  /content/drive/MyDrive/SerDataset/Tess/YAF_fea...   
1       fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...   
2       fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...   
3       fear  /content/drive/MyDrive/SerDataset/Crema/1055_I...   
4       fear  /content/drive/MyDrive/SerDataset/Tess/OAF_Fea...   
...      ...                                                ...   
1923    fear  /content/drive/MyDrive/SerDataset/Crema/1051_T...   
1924    fear  /content/drive/MyDrive/SerDataset/Crema/1044_M...   
1925    fear  /content/drive/MyDrive/SerDataset/Savee/DC_f06...   
1926    fear  /content/drive/MyDrive/SerDataset/Crema/1056_W...   
1927    fear  /content/drive/MyDrive/SerDataset/Crema/1056_T...   

            Latitude       Longitude  Latitude_DD  Longitude_DD  
0      N 8° 52′ 52''   E 76° 35′ 4''     8.881111     76.584444  
1      N 8° 57′ 24''   E 76° 51′ 9''     8.956667     76.852500

In [ ]:
# latitude = df['Latitude_DD'].values
# longitude = df['Longitude_DD'].values

In [ ]:
# coordinates = np.vstack([latitude, longitude])
# print(coordinates)

In [ ]:
# kde = gaussian_kde(coordinates)
# print(kde)

In [ ]:
# ax = plt.axes(projection=ccrs.PlateCarree())
# ax.stock_img()

new approach

In [ ]:
df.columns

Index(['Emotion', 'Path', 'Latitude', 'Longitude', 'Latitude_DD',
       'Longitude_DD'],
      dtype='object')

In [ ]:
m = folium.Map(location=[df.Latitude_DD.mean(), df.Longitude_DD.mean()],
                 zoom_start=6,
                 control_scale=True)
# Use a different tile provider
tile_provider = 'OpenStreetMap'  # Change to your preferred provider
folium.TileLayer(tile_provider).add_to(m)

# Disable caching (optional)
folium.TileLayer(tiles=tile_provider, caching=False).add_to(m)

In [ ]:
m

In [ ]:
m.save('simpleMap.html')

In [ ]:
#Add a single marker

folium.Marker(location=[df.Latitude_DD.mean(), df.Longitude_DD.mean()]).add_to(m)

In [ ]:
print(m)

In [ ]:
m

In [ ]:
m.save('simpleMap_meanLoc.html')

In [ ]:
folium.Marker(location=[df.Latitude_DD.mean(), df.Longitude_DD.mean()],
              icon=folium.Icon(color='red', icon='pushpin')).add_to(m)

In [ ]:
m

In [ ]:
#Loop through each row in the dataframe
for i,row in df.iterrows():
    #Setup the content of the popup
    iframe = folium.IFrame('Location:' + str(row["Emotion"]))

    #Initialise the popup using the iframe
    popup = folium.Popup(iframe, min_width=300, max_width=300)

    #Add each row to the map
    folium.Marker(location=[row['Latitude_DD'],row['Longitude_DD']],
                  popup = popup).add_to(m)

In [ ]:
m

In [ ]:
m.save('markerMap.html')

In [ ]:
from folium.plugins import MarkerCluster

# Create a map
m = folium.Map(location=[df['Latitude_DD'].mean(), df['Longitude_DD'].mean()], zoom_start=6)

# Create a MarkerCluster object
marker_cluster = MarkerCluster().add_to(m)

# Iterate through the DataFrame and add each row as a marker to the MarkerCluster
for i, row in df.iterrows():
    # Setup the content of the popup
    popup_content = 'Location: ' + str(row['Emotion'])

    # Create a popup using the content
    popup = folium.Popup(popup_content, min_width=300, max_width=300)

    # Add each row as a marker to the MarkerCluster
    folium.Marker(location=[row['Latitude_DD'], row['Longitude_DD']], popup=popup).add_to(marker_cluster)

# Display the map
m


In [ ]:
m.save('hotspot.html')

In [ ]:
# from geopy.geocoders import Nominatim

In [ ]:
# Loc = Nominatim(user_agent ="GetLoc")
# locname = Loc.reverse(())